# CommercialCompoundSearcher
An internal Sigman Lab tool for assessing the commercial availability of molecules based on the Pubchem database. We highly recommended to begin with a small subset (~25 molecules) to test the script first before using it on a larger dataset. Once a few variables are defined in later cells (like vendors to ignore), the script can be run autonomously by running all cells.


[https://github.com/thejameshoward/CommercialCompoundSearcher](https://github.com/thejameshoward/CommercialCompoundSearcher)

### Imports

In [1]:
# Built ins
import ast
import time
import urllib
from pathlib import Path
from pprint import pprint

# Data manipulation
import pandas as pd
import numpy as np

# Custom
from utils import canonicalize_smiles, smiles_to_inchi_key, smiles_to_inchi
from utils import remove_duplicate_inchi_keys
from utils import get_cid_from_inchi_key, get_vendor_list_from_cid
from utils import remove_specific_vendors_from_dataframe
from utils import draw_molecules_to_grid_image
from utils import convert_str_list
from utils import get_CAS_from_cid, get_SMILES_from_CAS
from utils import PubchemVendor


## Reading in list of smiles

The list of smiles can be a plaintext document with __SMILES__ in the first line and the '.txt' extension. Alternatively, the file extension could be '.csv' and also contain a __SMILES__ column.

```
┌────────────────────────┐
│ SMILES                 │
│ CC(=O)OCC[N+](C)(C)C   │
│ CC(C[N+](C)(C)C)OC(=O) │
│ ...                    │
└────────────────────────┘

```


In [ ]:
# Define a file
file = Path('./data/pyridines.csv')

# Read in the file
if file.suffix == '.txt':
    df = pd.read_table(file, header=0)
elif file.suffix == '.csv':
    df = pd.read_csv(file, header=0)
else:
    raise ValueError(f'{file.name} does not have a supported extension.')

# Check that the file is formatted correctly
if not 'SMILES' in df.columns:
    raise KeyError('The column "SMILES" should be in your provided spreadsheet or table.')

# Drop any empty rows
df.dropna(axis=0, how='any', inplace=True)

display(df)

## Canonicalization and additional molecular identifiers

This section is used to canonicalize the SMILES and add additional molecular identifier information using RDKit. The output of this block will contain warnings (and potentially errors) from RDKit. Many of these errors (such as None mol from RDKit) are handled by removing the SMILES string and storing it in a separate file. 

In [ ]:
# Apply canonicalization
#TODO Understand how this affects stereoisomerism in the SMILES/InChI/InChI key values
df['SMILES'] = df['SMILES'].apply(canonicalize_smiles)

# Add InChI column
df['INCHI'] = df['SMILES'].apply(smiles_to_inchi)

# Add InChI key column
df['INCHI_KEY'] = df['SMILES'].apply(smiles_to_inchi_key)

# Get every row that has np.nan values
failed = df[(df['INCHI'].isna()) | (df['INCHI_KEY'].isna())]

# Get every row that does not have np.nan values
df = df[~(df['INCHI'].isna()) | ~(df['INCHI_KEY'].isna())].copy(deep=True)

# Save the failed and the canonicalized datasets to a csv file
failed.to_csv('./results/failed_canonicalization.csv', index=False)
df.to_csv('./results/canonicalized.csv', index=False)

# Check if anything failed an notify the user
if failed.empty:
    print('No SMILES strings failed canonicalization.')
else:
    display(failed)

display(df)

## Remove duplicate InChI keys

Because we will be using REST queries to gather vendor information, it is important to remove duplicates because they will "waste" and REST query. This procedure removes __exact__ duplicates of the InChI key in the dataframe even if the SMILES string is different.

In [ ]:
# Remove exact duplicates
df, duplicates = remove_duplicate_inchi_keys(df=df)

# For your viewing pleasure
display(df)

if duplicates.empty:
    print('No duplicate entries were found.')
else:
    display(duplicates)

# Save the results for good book keeping.
df.to_csv('./results/added_molecular_identifiers.csv', index=False)
duplicates.to_csv('./results/duplicate_molecular_identifiers.csv', index=False)

## Query Pubchem for CID

The best identifier to use for querying Pubchem is the Pubchem Compound ID (CID). For more information on how Pubchem standardizes its database, please see the [compounds webpage](https://pubchem.ncbi.nlm.nih.gov/docs/compounds). This section will obtain a CID for a given InChi key. The REST queries each take at least 200 ms.

In [2]:
# Get inchi keys as a list
inchi_keys = df['INCHI_KEY'].to_list()

# Define a directory in which to store CID values
cid_dir = Path('./results/cids/')

# This assertion statement will fail if you have duplicate 
# InChi keys. If you don't care, remove the following line
assert len(list(set(inchi_keys))) == df.shape[0]

# Get the total length of InChI keys for tracking progress
total = len(inchi_keys)

# Enumerate over all inchi keys and add CID values
for i, inchi_key in enumerate(inchi_keys):

    if Path(cid_dir / inchi_key).exists():
        print(f'Found {inchi_key} in {cid_dir.absolute()}')
        with open(cid_dir / inchi_key, 'r') as _:
            cid = _.read()
    else:
        print(f'Working on {i + 1} of {total} ({round((i + 1) / total * 100, 2)}%)')

        # Set cid to nan if we can't find it
        cid = np.nan

        # Try to get the CID, if there is no CID, skip
        # This sleep here seems to prevent connection resets by Pubchem
        time.sleep(0.01)
        try:
            cid = get_cid_from_inchi_key(inchi_key)
            with open(cid_dir / inchi_key, 'w') as _:
                _.write(str(cid))
        except urllib.error.HTTPError as e:
            print(f'Could not convert InChi Key {inchi_key} to CID because {e}. Skipping.')
            continue
        except Exception as e:
            print(f'Could not convert InChi Key {inchi_key} to CID because {e}. Skipping.')
            continue

    # Check how many instances of that INCHI_KEY are in the df
    if df[df['INCHI_KEY'] == inchi_key].shape[0] != 1:
        print(f'WARNING: Found more than one InChI key {inchi_key}!')

    # Add the CID based on inchi_key
    df.loc[df['INCHI_KEY'] == inchi_key, 'CID'] = str(cid)

# Get the df of molecules for which there is no CID, save it for good book keeping
no_cids = df[df['CID'].astype(float).isna()]
no_cids.to_csv('./results/no_cid_found.csv', index=False)

# Get the new df that has CID values for each molecule, save it for for records
df = df[~(df['CID'].astype(float).isna())].copy(deep=True)
df.to_csv('./results/added_cid.csv', index=False)

display(df)

NameError: name 'df' is not defined

## Query Pubchem for vendors

This section will us the CID values found in the previous cell to acquire a list of vendors from Pubchem. The REST queries each take at least 200 ms.

In [3]:
df = pd.read_csv('./results/added_cid.csv', header=0)

# Get inchi keys as a list
cids = df['CID'].astype(int).to_list()

# Define a directory in which to store vendor information
vendor_dir = Path('./results/vendors/')

# This assertion statement will fail if you have duplicate 
# InChi keys. If you don't care, remove the following line
assert len(list(set(cids))) == df.shape[0]

# Get the total number of CIDs for tracking progress
total = len(cids)

# Keep a list of CIDs that have no vendors
no_vendor_cids = []

# Make a CID vendor dictionary that will contain the
# PubchemVendor objects
cid_vendor_dict = {}

# Enumerate over all CIDs and look for vendors
for i, cid in enumerate(cids):

    # Name the file for storing the vendor data
    vendor_file = Path(vendor_dir / f'{cid}.txt')

    # If the vendor information file already exists, read it in as a list of PubchemVendor instances
    if vendor_file.exists():
        print(f'Found {cid} in {vendor_dir.absolute()}')
        with open(vendor_file, 'r') as _:
            vendors = [PubchemVendor(cid, x) for x in ast.literal_eval(_.read())]
    else:
        print(f'Working on {i + 1} of {total} ({round((i + 1) / total * 100, 2)}%)')

        # Try to get the list of PubchemVendor objects
        try:
            vendors = list(set(get_vendor_list_from_cid(cid)))
            with open(vendor_file, 'w', encoding='utf-8') as _:
                _.write(str([v.vendor_info for v in vendors]))
        except urllib.error.HTTPError as e:
            print(f'Could not get vendor list from CID {cid}.')
            no_vendor_cids.append(int(cid))
            continue

    # Check how many instances of that CID are in the df
    if df[df['CID'].astype(int) == cid].shape[0] != 1:
        print(f'WARNING: Found more than one CID for {cid}!')

    # Add the CID/VENDORS based on inchi_key
    df.loc[df['CID'].astype(int) == cid, 'VENDORS'] = str([x.SourceName for x in vendors])

    # Add the CID:Vendor key:value pair
    cid_vendor_dict[cid] = vendors

# Get the df of molecules for which there are no vendors, save it for good book keeping
no_vendors = df[df['CID'].astype(int).isin(no_vendor_cids)].copy(deep=True)
no_vendors.to_csv('./results/no_vendors_found.csv')

# Get all the molecules that have vendors
df = df[~df['CID'].astype(int).isin(no_vendor_cids)]
df.to_csv('./results/with_vendors_found.csv', index=False)

display(df)

#print(cid_vendor_dict)

Found 75412451 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 53410241 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 63329927 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 46315299 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 12586779 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 22010197 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 822457 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 9942351 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 102545112 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher/results/vendors
Found 5200388 in /Users/jameshoward/Documents/Programming/CommercialCompoundSearcher

SMILES  Crippen_logp  NumHDonors  \
0       O=C1c2ccncc2C(O)N1c1c(Cl)cccc1Cl       3.03970           1   
1                   Cc1cc(Br)cnc1NCC(C)C       3.22042           1   
2                      Cc1ccncc1NC1CCSC1       2.30742           1   
3          FC(F)(F)c1ccc(-c2cccnc2)cc1Cl       4.42080           0   
4                CCCc1cc(C(=O)O)cc(Cl)n1       2.38570           1   
...                                  ...           ...         ...   
59642        O=C(c1ccc(=S)[nH]c1)N1CCCC1       1.98019           1   
59643   CCOC(=O)c1cnc2cc(F)c(F)c(F)c2c1O       2.53440           1   
59644   CCOC(=O)c1cnc2c(C(=O)OC)cccc2c1O       1.90370           1   
59645            COC(=O)c1c[nH]c(=S)cc1C       1.83921           1   
59646  O=C(O)c1ccc2nc(-c3cccnc3)[nH]c2c1       2.32310           2   

       NumHAcceptors  NumRotatableBonds   TPSA  natoms  refractivity  \
0                  3                  2  53.43      27       72.4683   
1                  2                  6  24.92      28       60.0017   
2                  3                  3  24.92      27       58.3267   
3                  1                  1  12.89      24       59.6850   
4                  3                  4  50.19      23       50.2013   
...              ...                ...    ...     ...           ...   
59642              2                  1  36.10      26       56.7642   
59643              4                  4  59.42      27       59.2383   
59644              6                  6  85.72      33       70.7038   
59645              3                  3  42.09      21       47.7032   
59646              4                  2  78.87      27       66.2840   

       HAS_PYR_H  HAS_MULTIPLE_PYR  HAS_FRAGMENTS  HAS_BAD_NITROGEN   MOL_WT  \
0           True             False          False             False  295.125   
1           True             False          False             False  243.148   
2           True             False          False             False  194.303   
3           True             False          False             False  257.642   
4           True             False          False             False  199.637   
...          ...               ...            ...               ...      ...   
59642       True             False          False             False  208.286   
59643       True             False          False             False  271.194   
59644       True             False          False             False  275.260   
59645       True             False          False             False  183.232   
59646       True             False          False             False  239.234   

       HAS_SULFONYL_HALIDE  HAS_ACID_HALIDES  HAS_PYRADINONE  \
0                    False             False           False   
1                    False             False           False   
2                    False             False           False   
3                    False             False           False   
4                    False             False           False   
...                    ...               ...             ...   
59642                False             False           False   
59643                False             False           False   
59644                False             False           False   
59645                False             False           False   
59646                False             False           False   

                                                   INCHI  \
0      InChI=1S/C13H8Cl2N2O2/c14-9-2-1-3-10(15)11(9)1...   
1      InChI=1S/C10H15BrN2/c1-7(2)5-12-10-8(3)4-9(11)...   
2      InChI=1S/C10H14N2S/c1-8-2-4-11-6-10(8)12-9-3-5...   
3      InChI=1S/C12H7ClF3N/c13-11-6-8(9-2-1-5-17-7-9)...   
4      InChI=1S/C9H10ClNO2/c1-2-3-7-4-6(9(12)13)5-8(1...   
...                                                  ...   
59642  InChI=1S/C10H12N2OS/c13-10(12-5-1-2-6-12)8-3-4...   
59643  InChI=1S/C12H8F3NO3/c1-2-19-12(18)5-4-16-7-3-6...   
59644  InChI=1S/C14H13NO5/c1-3-20-14(18)10-7-15-11-8(...  

## Filtering Vendors

The term "commercial availability" may differ between applications. Some vendors report that a compound is purchasable but will only synthesize it upon request. Additionally, the geographic location of the vendor's warehouse may lead to extended shipping times. In this section, we can filter vendors by selecting them from a list of total vendors.

The next cells are organized into separate steps.

In [20]:
# Print the total list of vendors
df = pd.read_csv('./results/with_vendors_found.csv')
list_of_current_vendors = list(set([vendor for vendor_list in df['VENDORS'].apply(convert_str_list) for vendor in vendor_list]))
display(f'UNIQUE VENDORS:')
pprint(list_of_current_vendors)
print(f'\nN_UNIQUE_VENDORS: {len(list_of_current_vendors)}')


'UNIQUE VENDORS:'

['10X CHEM',
 'Acemol',
 'Acadechem',
 'Acesobio',
 'Life Chemicals',
 'Nature Science Technologies Ltd',
 'NovoSeek',
 'Innovapharm',
 'Bangyong Technology  Co., Ltd.',
 'Boerchem',
 'Chemenu Inc.',
 'ChemBlock',
 'Apollo Scientific',
 'Tractus',
 'Synthonix, Inc.',
 'Lancrix Chemicals',
 'Exclusive Chemistry Ltd',
 'Zjartschem',
 'Synblock Inc',
 'Changzhou Naide Chemical',
 'Thoreauchem',
 'Alsachim',
 'Chemchart',
 'CHIRALEN',
 'ASINEX',
 'VWR, Part of Avantor',
 'Syntechem',
 'Syntech Labs',
 'AA BLOCKS',
 'Sarchem Laboratories, Inc.',
 'MolCore',
 'OtavaChemicals',
 'Wutech',
 'Sinfoo Biotech',
 'CoreSyn',
 'Assembly Blocks Pvt. Ltd.',
 'MedChemexpress MCE',
 'Rare Chemicals GmbH, Germany',
 'Sunwain',
 'Angene Chemical',
 'Aceschem Inc',
 'Combi-Blocks',
 'AmicBase - Antimicrobial Activities',
 'Moldb',
 'Parchem',
 'Aurum Pharmatech LLC',
 'BioCrick',
 'EvitaChem',
 '001Chemical',
 'TimTec',
 'Oakwood Products',
 'ChemExper Chemical Directory',
 'Vichem Chemie Ltd.',
 'Ace Ther

#### Select vendors to keep __OR__ vendors to remove

Two variables are declared below. Define one and only one of these variables to be a list of vendor strings. __This section relies on exact string comparison. Thus, it is important that the **exact** string is used from the block above.__ We recommend using VENDORS_TO_REMOVE to be more deliberate with vendor selection.

(experimental) We've included a list of vendors as a template for VENDORS_TO_KEEP.

In [21]:
# Define only one of these as a list
VENDORS_TO_KEEP = ['TCI (Tokyo Chemical Industry)',
 'Ambeed',
 'Combi-Blocks',
 'Thermo Fisher Scientific',
 'Sigma-Aldrich',
 'VWR, Part of Avantor']

VENDORS_TO_REMOVE = None

# Convert the string representation of the list of vendors
# to an actual Python list
df['VENDORS'] = df['VENDORS'].apply(convert_str_list)

# Get the list of current vendors (again)
list_of_current_vendors = list(set([vendor for vendor_list in df['VENDORS'].apply(convert_str_list) for vendor in vendor_list]))

# Convert vendors to keep into a vendors_to_remove list
if VENDORS_TO_REMOVE is None and VENDORS_TO_KEEP is not None:
    VENDORS_TO_REMOVE = [x for x in list_of_current_vendors if x not in VENDORS_TO_KEEP]

# Illegal options
elif VENDORS_TO_REMOVE is not None and VENDORS_TO_KEEP is not None:
    raise ValueError(f'Define either VENDORS_TO_REMOVE or VENDORS_TO_KEEP as a list not both.')

# User not removing any vendors
elif VENDORS_TO_REMOVE is None and VENDORS_TO_KEEP is None:
    VENDORS_TO_REMOVE = []

else:
    raise ValueError(f'Make sure you define the unused variable at the beginning of this cell to None')

# Remove the unwanted vendors
df = remove_specific_vendors_from_dataframe(df, vendors=VENDORS_TO_REMOVE)

# Purge empty df entries now
#TODO Reevaluate use of string literals as list intermediates
df = df[~(df['VENDORS'].astype(str) == '[]')]

display(df)


'''
# TODO Get the links from the vendor information from pubchem
# Get the new list of vendors
list_of_current_vendors = list(set([vendor for vendor_list in df['VENDORS'].to_list() for vendor in vendor_list]))
print(f'UNIQUE VENDORS:')
pprint(list_of_current_vendors)
print(f'\nN_UNIQUE_VENDORS: {len(list_of_current_vendors)}')

display(df)

for col in df.columns:
    print(df[col].dtype)
'''

SMILES  Crippen_logp  NumHDonors  \
0          O=C1c2ccncc2C(O)N1c1c(Cl)cccc1Cl       3.03970           1   
4                   CCCc1cc(C(=O)O)cc(Cl)n1       2.38570           1   
10               O=C(O)CNc1ccc(C(F)(F)F)cn1       1.59690           2   
11     CCOC(=O)c1cnc(Cl)c([N+](=O)[O-])c1Cl       2.47330           0   
13                 Fc1ccc(NCc2ccccn2)c(F)c1       2.97190           1   
...                                     ...           ...         ...   
59099    COC(=O)c1cc(O)c2cccc(C(F)(F)F)c2n1       2.74580           1   
59100           O=C(c1ccc(=S)[nH]c1)N1CCCC1       1.98019           1   
59101      CCOC(=O)c1cnc2cc(F)c(F)c(F)c2c1O       2.53440           1   
59102      CCOC(=O)c1cnc2c(C(=O)OC)cccc2c1O       1.90370           1   
59104     O=C(O)c1ccc2nc(-c3cccnc3)[nH]c2c1       2.32310           2   

       NumHAcceptors  NumRotatableBonds   TPSA  natoms  refractivity  \
0                  3                  2  53.43      27       72.4683   
4                  3                  4  50.19      23       50.2013   
10                 4                  3  62.22      22       45.3645   
11                 5                  4  82.33      22       56.8679   
13                 2                  3  24.92      26       57.9217   
...              ...                ...    ...     ...           ...   
59099              4                  3  59.42      27       59.7493   
59100              2                  1  36.10      26       56.7642   
59101              4                  4  59.42      27       59.2383   
59102              6                  6  85.72      33       70.7038   
59104              4                  2  78.87      27       66.2840   

       HAS_PYR_H  HAS_MULTIPLE_PYR  HAS_FRAGMENTS  HAS_BAD_NITROGEN   MOL_WT  \
0           True             False          False             False  295.125   
4           True             False          False             False  199.637   
10          True             False          False             False  220.150   
11          True             False          False             False  265.052   
13          True             False          False             False  220.222   
...          ...               ...            ...               ...      ...   
59099       True             False          False             False  271.194   
59100       True             False          False             False  208.286   
59101       True             False          False             False  271.194   
59102       True             False          False             False  275.260   
59104       True             False          False             False  239.234   

       HAS_SULFONYL_HALIDE  HAS_ACID_HALIDES  HAS_PYRADINONE  \
0                    False             False           False   
4                    False             False           False   
10                   False             False           False   
11                   False             False           False   
13                   False             False           False   
...                    ...               ...             ...   
59099                False             False           False   
59100                False             False           False   
59101                False             False           False   
59102                False             False           False   
59104                False             False           False   

                                                   INCHI  \
0      InChI=1S/C13H8Cl2N2O2/c14-9-2-1-3-10(15)11(9)1...   
4      InChI=1S/C9H10ClNO2/c1-2-3-7-4-6(9(12)13)5-8(1...   
10     InChI=1S/C8H7F3N2O2/c9-8(10,11)5-1-2-6(12-3-5)...   
11     InChI=1S/C8H6Cl2N2O4/c1-2-16-8(13)4-3-11-7(10)...   
13     InChI=1S/C12H10F2N2/c13-9-4-5-12(11(14)7-9)16-...   
...                                                  ...   
59099  InChI=1S/C12H8F3NO3/c1-19-11(18)8-5-9(17)6-3-2...   
59100  InChI=1S/C10H12N2OS/c13-10(12-5-1-2-6-12)8-3-4...   
59101  InChI=1S/C12H8F3NO

"\n# TODO Get the links from the vendor information from pubchem\n# Get the new list of vendors\nlist_of_current_vendors = list(set([vendor for vendor_list in df['VENDORS'].to_list() for vendor in vendor_list]))\nprint(f'UNIQUE VENDORS:')\npprint(list_of_current_vendors)\nprint(f'\nN_UNIQUE_VENDORS: {len(list_of_current_vendors)}')\n\ndisplay(df)\n\nfor col in df.columns:\n    print(df[col].dtype)\n"

#### Save the curated list of molecules

In [22]:
list_of_current_vendors = list(set([vendor for vendor_list in df['VENDORS'].apply(convert_str_list) for vendor in vendor_list]))

# Add a link for each current vendor
for v in list_of_current_vendors:
    df[f'{v}_link'] = 'NONE'

rows = []
for i, row in df.iterrows():
    # For each vendor that sells that row
    for vendor_name in row['VENDORS']:
        all_vendor_objects = cid_vendor_dict[row['CID']]
        all_vendor_objects = [x for x in all_vendor_objects if x.SourceName == vendor_name]
        if len(all_vendor_objects) == 0:
            continue
        row[f'{vendor_name}_link'] = all_vendor_objects[0].SourceRecordURL
    rows.append(row)

df = pd.DataFrame(rows)
display(df)
df.to_csv('./results/with_vendor_links.csv', index=False)

SMILES  Crippen_logp  NumHDonors  \
0          O=C1c2ccncc2C(O)N1c1c(Cl)cccc1Cl       3.03970           1   
4                   CCCc1cc(C(=O)O)cc(Cl)n1       2.38570           1   
10               O=C(O)CNc1ccc(C(F)(F)F)cn1       1.59690           2   
11     CCOC(=O)c1cnc(Cl)c([N+](=O)[O-])c1Cl       2.47330           0   
13                 Fc1ccc(NCc2ccccn2)c(F)c1       2.97190           1   
...                                     ...           ...         ...   
59099    COC(=O)c1cc(O)c2cccc(C(F)(F)F)c2n1       2.74580           1   
59100           O=C(c1ccc(=S)[nH]c1)N1CCCC1       1.98019           1   
59101      CCOC(=O)c1cnc2cc(F)c(F)c(F)c2c1O       2.53440           1   
59102      CCOC(=O)c1cnc2c(C(=O)OC)cccc2c1O       1.90370           1   
59104     O=C(O)c1ccc2nc(-c3cccnc3)[nH]c2c1       2.32310           2   

       NumHAcceptors  NumRotatableBonds   TPSA  natoms  refractivity  \
0                  3                  2  53.43      27       72.4683   
4                  3                  4  50.19      23       50.2013   
10                 4                  3  62.22      22       45.3645   
11                 5                  4  82.33      22       56.8679   
13                 2                  3  24.92      26       57.9217   
...              ...                ...    ...     ...           ...   
59099              4                  3  59.42      27       59.7493   
59100              2                  1  36.10      26       56.7642   
59101              4                  4  59.42      27       59.2383   
59102              6                  6  85.72      33       70.7038   
59104              4                  2  78.87      27       66.2840   

       HAS_PYR_H  HAS_MULTIPLE_PYR  ...  \
0           True             False  ...   
4           True             False  ...   
10          True             False  ...   
11          True             False  ...   
13          True             False  ...   
...          ...               ...  ...   
59099       True             False  ...   
59100       True             False  ...   
59101       True             False  ...   
59102       True             False  ...   
59104       True             False  ...   

                                                   INCHI  \
0      InChI=1S/C13H8Cl2N2O2/c14-9-2-1-3-10(15)11(9)1...   
4      InChI=1S/C9H10ClNO2/c1-2-3-7-4-6(9(12)13)5-8(1...   
10     InChI=1S/C8H7F3N2O2/c9-8(10,11)5-1-2-6(12-3-5)...   
11     InChI=1S/C8H6Cl2N2O4/c1-2-16-8(13)4-3-11-7(10)...   
13     InChI=1S/C12H10F2N2/c13-9-4-5-12(11(14)7-9)16-...   
...                                                  ...   
59099  InChI=1S/C12H8F3NO3/c1-19-11(18)8-5-9(17)6-3-2...   
59100  InChI=1S/C10H12N2OS/c13-10(12-5-1-2-6-12)8-3-4...   
59101  InChI=1S/C12H8F3NO3/c1-2-19-12(18)5-4-16-7-3-6...   
59102  InChI=1S/C14H13NO5/c1-3-20-14(18)10-7-15-11-8(...   
59104  InChI=1S/C13H9N3O2/c17-13(18)8-3-4-10-11(6-8)1...   

                         INCHI_KEY       CID  \
0      KIWHDIYRJPWJOA-UHFFFAOYSA-N  75412451   
4      ADZGFLWGSFWWDY-UHFFFAOYSA-N  12586779   
10     BLWLBHNBENFLEA-UHFFFAOYSA-N  16228265   
11     VMNMZVKEDHEOEJ-UHFFFAOYSA-N  21781755   
13     WNIFZTLYRMLXLG-UHFFFAOYSA-N  28477339   
...                            ...       ...   
59099  YQFLSLNXTHQDHJ-UHFFFAOYSA-N  46738876   
59100  SRWHCIKMKOGGRD-UHFFFAOYSA-N  17476062   
59101  SREYUBSTHJZZGQ-UHFFFAOYSA-N  54595638   
59102  ULYDEAPQWZWKJY-UHFFFAOYSA-N    720005   
59104  DHRPCXYIVJXXJR-UHFFFAOYSA-N   2771805   

                                                 VENDORS  \
0                                 [Combi-Blocks, Ambeed]   
4                                               [Ambeed]   
10                                        [Combi-Blocks]   
11                                [Combi-Blocks, Ambeed]   
13                                [Ambeed, Combi-Blocks]   
...                                                  ...   
59099               [Combi-Blocks, Combi-Blocks, Ambeed]   


In [ ]:
df.to_csv('./FINAL_LIBRARY_CURATED.csv', index=False)

## Query Pubchem for CAS number

This section will us the CID values found in the previous cells to acquire a CAS number from Pubchem. Often a molecule will have multiple CAS numbers and the `get_CAS_from_CID()` function will gather only one of them. Users should be aware that this looks for two dashes (-) in the numbers it receives from Pubchem to identify the CAS number. This procedure could be improved by a more systematic way of determining whether the item received from Pubchem is actually a CAS number. The REST queries each take at least 200 ms.

__If you stop this cell while it is running, you will lose all of your progress towards acquiring vendors__

In [ ]:
# Get the full list of CIDs from the library
cids = [int(x) for x in df['CID'].to_list() if x != '']

# Get the total number of CIDs for tracking progress
total = len(cids)

# Keep a list of CIDs that have no vendors
no_vendor_cids = []

# Enumerate over all CIDs and look for vendors
for i, cid in enumerate(cids):
    print(f'Working on {i + 1} of {total} ({round((i + 1) / total * 100, 2)}%)')

    # Try to get the list of PubchemVendor objects
    try:
        cas = get_CAS_from_cid(cid)
    except urllib.error.HTTPError as e:
        print(f'Could not get CAS number from CID {cid}. ERROR: {e}')
        continue

    # Add the CID/VENDORS based on inchi_key
    df.loc[df['CID'].astype(int) == cid, 'CAS_NUMBER'] = str(cas)

    # Check how many instances of that CID are in the df
    #if df[df['CID'].astype(int) == cid].shape[0] != 1:
    #    print(df[df['CID'] == cid])
    #    print(f'WARNING: Found more than one CID for {cid}!')
    ## Add the CID/VENDORS based on inchi_key
    #df.loc[df['CID'].astype(int) == cid, 'CAS'] = str(cas)

# Save the file 
df.to_csv('./FINAL_LIBRARY_CURATED_with_cas_numbers.csv', index=False)



## Query a Sigman Inventory Export for the CAS numbers

Export a full copy of the Sigman inventory in labsuit and point the inventory_spreadsheet variable to its path. This cell will create a slice of the dataframe that contains CAS numbers in both your curated library and the inventory spreadsheet.

In [ ]:
# Define the spreadsheet file
inventory_spreadsheet = Path('./data/Sigman-inventory-03-07-2024-example.xlsx')

# Read in the file (These settings should read the default format)
try:        
    inventory = pd.read_excel(file, header=0, sheet_name='Chemical', engine='openpyxl')
except Exception: # This is required because I think labsuit is not zipping their xlsx files
    with open(inventory_spreadsheet, 'rb') as infile:
        inventory = pd.read_excel(infile, sheet_name='Chemical')

# Filter inventory by presence of CAS
inventory['CAS_NUMBER'] = inventory['CAS_NUMBER'].astype(str).apply(str.strip)
inventory = inventory[inventory['CAS_NUMBER'].astype(str).isin(df['CAS_NUMBER'])]

display(inventory)

# Save the owned molecules in the results folder
inventory.to_csv('./results/owned_molecules.csv', index=False)

## Query Pubchem for SMILES from CAS Number

In [ ]:

# Define the spreadsheet file
inventory_spreadsheet = Path('./data/Sigman-inventory-03-07-2024-example.xlsx')

# Read in the file (These settings should read the default format)
try:        
    inventory = pd.read_excel(file, header=0, sheet_name='Chemical', engine='openpyxl')
except Exception: # This is required because I think labsuit is not zipping their xlsx files
    with open(inventory_spreadsheet, 'rb') as infile:
        inventory = pd.read_excel(infile, sheet_name='Chemical')

# Get the full list of CAS from the library
CAS_NUMBERS = [str(x) for x in inventory['CAS_NUMBER'].to_list() if x != '']

# Get the total number of CAS for tracking progress
total = len(CAS_NUMBERS)

# Keep a list of CAS numbers for which we could get no SMILES
no_vendor_cids = []

# Enumerate over all CAS and look for vendors
for i, CAS in enumerate(CAS_NUMBERS):
    print(f'Working on {i + 1} of {total} ({round((i + 1) / total * 100, 2)}%)')

    # Try to get the list of PubchemVendor objects
    try:
        smiles = get_SMILES_from_CAS(CAS)
    except urllib.error.HTTPError as e:
        print(f'Could not get SMILES string from CAS {cas}. ERROR: {e}')
        continue

    # Add the CID/VENDORS based on inchi_key
    inventory.loc[inventory['CAS_NUMBER'].astype(str) == CAS, 'SMILES'] = str(smiles)

# Save the file 
inventory.to_csv('./Inventory_with_smiles.csv', index=False)



## Drawing molecules 🥳 !

In this section we've included some useful functions for drawing molecules in your library.

In [ ]:
# Get a list of all smiles
smiles = df['SMILES'].to_list()

print(f'Number of SMILES: {len(smiles)}')

smiles = smiles[:1000]

# Get the PIL images of the grid by passing smiles list
images = draw_molecules_to_grid_image(smiles, mols_per_row=6, img_resolution=600)

for image in images:
    display(image)